In [222]:
import numpy as np
import simpy
import random
import matplotlib
import pandas as pd

In [290]:
SEED = 930
UNIFORM_INTERVAL = [4.17, 5.37]
NUM_SERVER = 2
SERVER_UTILIZATIONS_PHASE1 = [0.6, 0.7, 0.8, 0.9]
SERVER_SERVICE_MEAN_PHASE1 = [5.725,6.679,7.634,8.588]
SERVER_UTILIATION_PHASE2 = [0.8]
NUMBER_OF_CUSTOMERS = 300


In [291]:
phase_1_lib = {"num_server":NUM_SERVER,"arr_interval":UNIFORM_INTERVAL,"util":SERVER_UTILIZATIONS_PHASE1,"serv_mean":SERVER_SERVICE_MEAN_PHASE1}
phase_2_lib = {"num_server":NUM_SERVER,"arr_interval":UNIFORM_INTERVAL,"util":SERVER_UTILIATION_PHASE2,"serv_mean":[7.634]}

In [292]:
class Job(object):
    def __init__(self, name, env, operator , run_):
        self.env = env
        self.name = name
        self.operator = operator
        self.arrival_t = self.env.now
        self.action = self.env.process(self.call())
        self.run = run_
        
    
    def call(self):
        print('%s initiated at %g' % (self.name, self.env.now))
        self.run.num_jobs_c += 1
        self.run.num_jobs_system[-1][2] = self.env.now
        self.run.num_jobs_system.append([self.run.num_jobs_c,self.env.now,-1])
 
        with self.operator.request() as req:
            yield req
            print('%s is assigned to an operator at %g' % (self.name, self.env.now))
            self.run.queue_w_times.append(self.env.now - self.arrival_t)
            yield self.env.process(self.progress_job())
            print('%s is done at %g' % (self.name, self.env.now))
            self.departure_t = self.env.now
            self.run.num_jobs_c -= 1
            self.run.num_jobs_system[-1][2] = self.env.now
            self.run.num_jobs_system.append([self.run.num_jobs_c,self.env.now,-1])

            
    def progress_job(self):
        duration = random.expovariate(self.run.serv_rate)
        yield self.env.timeout(duration)
        self.run.service_times.append(duration)
        

In [293]:
class Run():
    def __init__(self,arr_rate,serv_rate,start_job):
        self.start_job = start_job
        self.seed = random.random()*930
        self.run = False
        self.arr_rate = arr_rate
        self.serv_rate = 1/serv_rate
        self.num_jobs_c = 0
        self.num_jobs_system = [[0,0,-1]]
        self.jobs=[]
        self.service_times=[]
        self.queue_w_times=[]
        self.env = simpy.Environment()
        self.operator = simpy.Resource(self.env, capacity = NUM_SERVER)
    

    def run_sim(self):
        random.seed(self.seed)
        self.env.process(self.jobs_generator())
        self.env.run()
        self.run = True
        self.average_num_jobs_system()
        
    def show_run(self):
        if self.run!=True:
            self.run_sim()
        
    def average_num_jobs_system(self):
        weighted_value =0
        for arr in self.num_jobs_system:
            if(arr[2]==-1):
                end_of_sim = arr[1]
                break
            weighted_value += arr[0]*(arr[2]-arr[1])
        self.avg_jobs = weighted_value / end_of_sim

    def jobs_generator(self):
        if(self.start_job != 0):
            for i in range(self.start_job):
                yield self.env.timeout(0)
                job = Job('Job %s' %(i+1), self.env, self.operator,self)
                self.jobs.append(job)
            
            for k in range(NUMBER_OF_CUSTOMERS-self.start_job):
                yield self.env.timeout(random.uniform(4.17,5.37))
                job = Job('Job %s' %(k+1+self.start_job), self.env, self.operator,self)
                self.jobs.append(job)  
        else:        
            for i in range(NUMBER_OF_CUSTOMERS):
                yield self.env.timeout(random.uniform(4.17,5.37))
                job = Job('Job %s' %(i+1), self.env, self.operator,self)
                self.jobs.append(job)  

In [294]:
class Phase():
    def __init__(self,lib,num_runs,start):
        self.start = start
        self.num_server = lib["num_server"]
        self.arr_int = 1/((lib["arr_interval"][0]+lib["arr_interval"][1])/2)
        self.util = lib["util"]
        self.serv_mean = lib["serv_mean"]
        self.init_runs(num_runs)
        self.num_runs = num_runs

    def init_runs(self,num_runs):
        self.runs = []
        for util_no in range(len(self.util)):
            for i in range(num_runs):
                obj = Run(self.arr_int,self.serv_mean[util_no],self.start)
                self.runs.append(obj)

    def run_phase(self):
        for run in self.runs:
            run.run_sim()
            
        print("total run :",len(self.runs)," ")
    
    def create_df(self,util):
        for i in range(len(self.ens_avg[util])):
            if(i == 0):
                ens_sum_avg = [self.ens_avg[util][0]]
                ens_cum_avg = [self.ens_avg[util][0]]
            else:
                ens_sum_avg.append((ens_sum_avg[len(ens_sum_avg)-1]+self.ens_avg[util][i])) 
                ens_cum_avg.append((ens_sum_avg[len(ens_sum_avg)-1]/(i+1)))
        df_arr_avg = pd.DataFrame(self.arr_avg[util],columns=["ARRIVAL"])
        df_ens_avg = pd.DataFrame(self.ens_avg[util],columns=["AVG"])
        df_ens_sum_avg = pd.DataFrame(ens_sum_avg,columns=["SUM-AVG"])
        df_ens_cum_avg = pd.DataFrame(ens_cum_avg,columns=["CUM-AVG"])
        df = pd.concat([df_arr_avg,df_ens_avg,df_ens_sum_avg,df_ens_cum_avg],ignore_index=True,axis=1)

        selected_runs = self.runs[(util)*self.num_runs:(util+1)*self.num_runs]
        
        for run_no, run in enumerate(selected_runs):
            df_time_spend = pd.DataFrame(np.sum([run.service_times,run.queue_w_times],axis=0),columns=["REPLICATION-"+str(run_no)])
            
            
            df = pd.concat([df,df_time_spend],ignore_index=True,axis=1)
        
        return df

    def arrival_averages(self):
        self.arr_avg = [[0 for i in range(NUMBER_OF_CUSTOMERS)] for j in range(len(self.util))]
        for util_no in range(len(self.util)):
            for run_no in range(self.num_runs):
                for i in range(NUMBER_OF_CUSTOMERS):
                    self.arr_avg[util_no][i] = self.arr_avg[util_no][i] + self.runs[util_no*self.num_runs+run_no].jobs[i].arrival_t
        self.arr_avg = np.divide(self.arr_avg,self.num_runs)

    def ensemble_averages(self):
        self.ens_avg = [[0 for i in range(NUMBER_OF_CUSTOMERS)] for j in range(len(self.util))]
        for k in range(len(self.util)):
            for run_no in range(self.num_runs):
                for i in range(NUMBER_OF_CUSTOMERS):
                    self.ens_avg[k][i] = self.ens_avg[k][i] + (self.runs[k*self.num_runs+run_no].service_times[i] + self.runs[k*self.num_runs+run_no].queue_w_times[i])
        self.ens_avg = np.divide(self.ens_avg,self.num_runs)
            

In [295]:
phase_1 = Phase(phase_1_lib,10)
phase_1_30 = Phase(phase_1_lib,30)

TypeError: Phase.__init__() missing 1 required positional argument: 'start'

In [296]:
phase_1.run_phase()
phase_1_30.run_phase()

Job 1 initiated at 1459.19
Job 1 is assigned to an operator at 1459.19
Job 2 initiated at 1464.42
Job 2 is assigned to an operator at 1464.42
Job 2 is done at 1465.24
Job 1 is done at 1469.03
Job 3 initiated at 1469.29
Job 3 is assigned to an operator at 1469.29
Job 4 initiated at 1473.67
Job 4 is assigned to an operator at 1473.67
Job 4 is done at 1473.86
Job 5 initiated at 1478.07
Job 5 is assigned to an operator at 1478.07
Job 5 is done at 1480.68
Job 6 initiated at 1483.27
Job 6 is assigned to an operator at 1483.27
Job 6 is done at 1486.87
Job 7 initiated at 1488.3
Job 7 is assigned to an operator at 1488.3
Job 3 is done at 1488.56
Job 7 is done at 1490.07
Job 8 initiated at 1492.87
Job 8 is assigned to an operator at 1492.87
Job 8 is done at 1495.69
Job 9 initiated at 1497.34
Job 9 is assigned to an operator at 1497.34
Job 9 is done at 1501.01
Job 10 initiated at 1502.42
Job 10 is assigned to an operator at 1502.42
Job 10 is done at 1505.78
Job 11 initiated at 1506.81
Job 11 is a

In [297]:
phase_1.ensemble_averages()
phase_1.arrival_averages()

phase_1_30.ensemble_averages()
phase_1_30.arrival_averages()

In [298]:
phase_1.ensemble_averages
phase_1_30.ensemble_averages

<bound method Phase.ensemble_averages of <__main__.Phase object at 0x1378ec550>>

In [299]:
df_0 = phase_1.create_df(0)
df_1 = phase_1.create_df(1)
df_2 = phase_1.create_df(2)
df_3 = phase_1.create_df(3)
df_0.to_csv("df_0.6_10.csv")
df_1.to_csv("df_0.7_10.csv")
df_2.to_csv("df_0.8_10.csv")
df_3.to_csv("df_0.9_10.csv")

df_0_30 = phase_1_30.create_df(0)
df_1_30 = phase_1_30.create_df(1)
df_2_30 = phase_1_30.create_df(2)
df_3_30 = phase_1_30.create_df(3)
df_0_30.to_csv("df_0.6_30.csv")
df_1_30.to_csv("df_0.7_30.csv")
df_2_30.to_csv("df_0.8_30.csv")
df_3_30.to_csv("df_0.9_30.csv")

In [300]:
run = phase_1.runs[1]
for i in range(len(run.jobs)):
    if i == 0:
        arrival_sum = run.jobs[i].arrival_t
    else:
        arrival_sum = arrival_sum + (run.jobs[i].arrival_t - run.jobs[i-1].arrival_t)

arrival_sum = arrival_sum / 1000
arrival_sum

2.8855435659963717

In [301]:
run= phase_1.runs[1]
summ= np.mean(run.service_times)
summ  

5.709728731767891

In [306]:
phase_2_1 = Phase(phase_2_lib,1,0)
phase_2_1.run_phase()
phase_2_1.ensemble_averages()
phase_2_1.arrival_averages()
df_case_1 = phase_2_1.create_df(0)
df_case_1.to_csv("phase_2_case1.csv")
83

phase_2_2 = Phase(phase_2_lib,1,4)
phase_2_2.run_phase()
phase_2_2.ensemble_averages()
phase_2_2.arrival_averages()
df_case_2 = phase_2_2.create_df(0)
df_case_2.to_csv("phase_2_case2.csv")

NUMBER_OF_CUSTOMERS = 103 #83 + 20
phase_2_3 = Phase(phase_2_lib,1,0)
phase_2_3.run_phase()
phase_2_3.ensemble_averages()
phase_2_3.arrival_averages()
df_case_3 = phase_2_3.create_df(0)
df_case_3.to_csv("phase_2_case3.csv")

Job 1 initiated at 4.51706
Job 1 is assigned to an operator at 4.51706
Job 1 is done at 5.33048
Job 2 initiated at 9.5069
Job 2 is assigned to an operator at 9.5069
Job 3 initiated at 14.4909
Job 3 is assigned to an operator at 14.4909
Job 2 is done at 17.0378
Job 4 initiated at 18.8406
Job 4 is assigned to an operator at 18.8406
Job 3 is done at 19.1622
Job 5 initiated at 23.8838
Job 5 is assigned to an operator at 23.8838
Job 5 is done at 24.329
Job 6 initiated at 28.3093
Job 6 is assigned to an operator at 28.3093
Job 6 is done at 29.0252
Job 7 initiated at 33.0156
Job 7 is assigned to an operator at 33.0156
Job 8 initiated at 38.0057
Job 7 is done at 40.242
Job 8 is assigned to an operator at 40.242
Job 8 is done at 41.5692
Job 9 initiated at 42.6035
Job 9 is assigned to an operator at 42.6035
Job 9 is done at 43.0936
Job 4 is done at 43.1202
Job 10 initiated at 46.9601
Job 10 is assigned to an operator at 46.9601
Job 10 is done at 51.6235
Job 11 initiated at 51.6427
Job 11 is assi

In [307]:
for job in phase_2_2.runs[0].jobs:
    print(job.arrival_t)

0
0
0
0
4.19125569537298
9.128434960817518
14.150675682085105
19.26954585181026
23.965860934040514
29.307279291187594
33.55426429561352
38.54818365270364
43.234261003301306
47.94632327906575
52.394840658601645
57.49136268565972
62.09836625217685
67.20689309717008
71.74539478151769
76.82087534661048
81.14480479289504
85.6071159661732
90.84521568383774
95.72303871257515
100.43946723656892
105.50358115749341
110.43394400076676
114.8702676670061
119.19560771541286
123.59386928282358
128.35131506535612
132.57881417025789
136.862362954804
142.16432165707562
146.8044118400009
151.13456546371165
155.81175735422153
160.54216036573163
165.32455922016092
169.82918663288612
174.84963202988328
179.1294259167846
184.40684910349165
189.73438372973763
194.66932634453832
199.9991721473925
204.58043152086796
208.84463394575013
213.6762238204458
218.85813818557148
223.86667913527714
228.2194765228062
233.51743987171133
238.6829626452521
243.24606068520112
248.3825211152043
252.8747721638738
257.724522839